In [16]:
import pandas as pd
import numpy as np
import random as rnd
import seaborn as sns
!pip install fuzzywuzzy
from fuzzywuzzy import fuzz
import collections
 
pd.set_option("display.max_columns",None)
pd.set_option("display.max_rows",None)

In [17]:
# Gathering preliminary info of our dataset to proceed further with data processing

# In the first part we will be predicting the type of course given other features
# We notice that Ingredients, Diet, Course, Price/Unit have no missing values 
data=pd.read_csv("Data.csv") 
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 255 entries, 0 to 254
Data columns (total 10 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Name              255 non-null    object 
 1   Ingradients       255 non-null    object 
 2   Diet              255 non-null    object 
 3   Preparation Time  225 non-null    float64
 4   Cooking Time      227 non-null    float64
 5   Flavor            226 non-null    object 
 6   Course            255 non-null    object 
 7   State             231 non-null    object 
 8   Region            241 non-null    object 
 9   Price/unit        255 non-null    int64  
dtypes: float64(2), int64(1), object(7)
memory usage: 20.0+ KB


In [18]:
# Dropping all rows with NaN will result in loss of almost 30% of the data present (180/225 *100 % data is left)
# Since many features have no NaNs, we will try to retrieve rows with NaNs through various imputations
data.dropna().info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 180 entries, 0 to 253
Data columns (total 10 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Name              180 non-null    object 
 1   Ingradients       180 non-null    object 
 2   Diet              180 non-null    object 
 3   Preparation Time  180 non-null    float64
 4   Cooking Time      180 non-null    float64
 5   Flavor            180 non-null    object 
 6   Course            180 non-null    object 
 7   State             180 non-null    object 
 8   Region            180 non-null    object 
 9   Price/unit        180 non-null    int64  
dtypes: float64(2), int64(1), object(7)
memory usage: 15.5+ KB


In [19]:
# data.groupby(['Diet','Region'])['Preparation Time'].apply(lambda x: x.fillna(x.mean()))

# Before starting with filling NaNs, we do some elementary cleaning

data=data.drop(columns=['Name','State'])
# We drop Name since we are asked to do so according to the problem statement
# We drop State because we already have a Region feature present which has the states aggregated in groups 
# Moreover when we finally do one hot encoding of categorical variables using State would unnecessarily 
# increase the number of columns. Also, there are fewer Nans in Region as compared to State.

data=data.rename(columns={'Ingradients':'Ingredients'})
# Correcting the name of Ingredients for future use


In [20]:
# We will first try to fill NaNs of Prep and Cook Time
# For doing this we try finding its correlation with Price/Unit (since it is ony numerical feature present) and 

# finding its mean/median when grouping with region/ flavor/ diet
# But again flavor has many NaNs and considering the imputed values will bring more randomness to imputation of prep/cook time
# and we also reason that total time taken for a dish should be uncorrelated to flavor
 
test=data.dropna(subset=["Cooking Time","Preparation Time"])
test.corr()

Preparation Time  Cooking Time  Price/unit
Preparation Time           1.00000      0.110780   -0.038180
Cooking Time               0.11078      1.000000   -0.000187
Price/unit                -0.03818     -0.000187    1.000000

In [21]:
# We find that price is in fact slightly negatively correlated to prep/cook time. We will discard price for imputation 

# Lets try for Diet
data[['Preparation Time','Cooking Time','Diet']].groupby(['Diet'], as_index=False).mean()

# Clearly non-vegetarian food on average takes more time to prepare(due to long hours of marination)
# and cook (because ambient internal temperature has to be maintained to kill bacteria present in raw flesh)

Diet  Preparation Time  Cooking Time
0  non vegetarian         41.842105       40.0000
1      vegetarian         34.791262       38.8125

In [22]:
data[['Preparation Time', 'Cooking Time','Region']].groupby(['Region'], as_index=False).mean()

Region  Preparation Time  Cooking Time
0     Central         13.333333     48.333333
1        East         43.518519     41.607143
2       North         38.020833     41.979167
3  North East         28.846154     28.461538
4       South         58.181818     36.909091
5        West         16.924242     41.880597

In [23]:
data[['Preparation Time','Cooking Time', 'Diet','Region']].groupby(['Diet','Region'], as_index=False).median()

Diet      Region  Preparation Time  Cooking Time
0   non vegetarian        East              12.5          37.5
1   non vegetarian       North             120.0          35.0
2   non vegetarian  North East              10.0          22.5
3   non vegetarian       South              10.0          60.0
4   non vegetarian        West              10.0          40.0
5       vegetarian     Central              10.0          45.0
6       vegetarian        East              20.0          42.5
7       vegetarian       North              15.0          40.0
8       vegetarian  North East              10.0          30.0
9       vegetarian       South              10.0          30.0
10      vegetarian        West              10.0          30.0

In [24]:

data=data.dropna(subset=['Region'])
# Now, we dropna of Region before filling NaNs
# Doing this we lose 14 rows out of 225 rows. Hence, a loss of ~6 percent of data
# Great work in reducing the data loss from 30 percent to 6 percent!!

data=data.reset_index(drop=True)

In [25]:
# Finally filling NaNs of Prep and Cook Time with the median after grouping by diet and region

data['Preparation Time']=data['Preparation Time'].fillna(data.groupby(['Diet','Region'])['Preparation Time'].transform('median'))
data['Cooking Time']=data['Cooking Time'].fillna(data.groupby(['Diet','Region'])['Cooking Time'].transform('median'))

In [26]:
# Now,we will try to fill Nans of Flavor
data["Flavor"].isna().sum()

27

In [27]:
# Notice that sour and bitter have almost negligible appearance in the dataset, which is heavily dominated by spicy 
data["Flavor"].value_counts().sort_values(ascending=True)

sour        1
bitter      4
sweet      82
spicy     127
Name: Flavor, dtype: int64

In [28]:
# In the following function, we will uniformly randomly fill Flavor NaNs from a list 
# that emulates the frequencies of the categorical variables of Flavor
def fill_freq(freq):
  dct={}
  lst=[]
  curr=0
  for idx,flav in enumerate(freq.index):
    dct[curr]=flav
    ct=freq[idx]
    lst=lst+[curr]*ct
    curr+=1
  rnd.shuffle(lst)
  return [dct,lst]

pair=fill_freq(data['Flavor'].value_counts().sort_values(ascending=True))

for idx,x in enumerate(data["Flavor"].isna()):
  if(x):
    temp=pair[1][rnd.randint(0,len(pair[1])-1)]
    data['Flavor'][idx]=pair[0][temp]

<ipython-input-28-8e7e9573ec37>:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Flavor'][idx]=pair[0][temp]


In [29]:
# We get a dataset with minimal losses retaining 241 of 255 rows !!
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 241 entries, 0 to 240
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Ingredients       241 non-null    object 
 1   Diet              241 non-null    object 
 2   Preparation Time  241 non-null    float64
 3   Cooking Time      241 non-null    float64
 4   Flavor            241 non-null    object 
 5   Course            241 non-null    object 
 6   Region            241 non-null    object 
 7   Price/unit        241 non-null    int64  
dtypes: float64(2), int64(1), object(5)
memory usage: 15.2+ KB


In [32]:
data["Total"]=data["Preparation Time"]+data["Cooking Time"]

In [33]:
data[['Total', 'Course']].groupby(['Course'], as_index=False).mean().sort_values(by="Total")

Course       Total
1  main course   61.880000
0      dessert   76.829114
2        snack   90.600000
3      starter  217.500000

In [34]:
# Spilling strings in Ingredients column into individual string which will be merged to the dataframe 
# after One Hot encoding and performing PCA on the set of ingredients

ing_dic = collections.defaultdict(int)
food=data
for f in food.index:
    ing_list = food.at[f, 'Ingredients'].split(', ')
    for i in ing_list:
        i = i.lower().strip()
        ing_dic[i] += 1

ing_df = pd.DataFrame.from_dict(ing_dic, orient='index')\
    .rename(columns={0:'count'})

In [42]:
# We find a total of 352 ingredients
ing_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 352 entries, maida flour to ginger powder
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   count   352 non-null    int64
dtypes: int64(1)
memory usage: 5.5+ KB


In [35]:
# But we notice that same ingredients are present with a variety of names in the list of ingredients found

ing_df.sort_index().loc['red': 'red0'].T
# ing_df.sort_index()

red chili  red chilli  red chillies  red food coloring  \
count          1           4             1                  1   

       red kidney beans  red onion  
count                 2          3

In [36]:
# Our strategy will be to perform a string matching algortirhm like SOUNDEX or Fuzzy matching 
# on the list of ingredients to find the common ingredients with different names

# Here, we move forward with Fuzzy matching because according to Wikipedia Fuzzy matching achieves higher benchmarks
# For this purpose we will be using the FuzzyWuzzy library 


similar={}
ing_list = ing_df.sort_values('count').index.to_list()
n = 0
for i in range(len(ing_list)-1):
    for j in range(i+1, len(ing_list)):
        ratio = fuzz.ratio(ing_list[i], ing_list[j])
        # if n == 30:
        #     break
        if ratio >=66:
            # print(ing_list[i], ', ', ing_list[j], '\t', ratio)
            similar[ing_list[i]]=ing_list[j]
            n += 1

In [37]:
# On setting a threshold of 0.66, we found a large dict of matches according to our strategy
# Obviously we would have to now apply our domain knowledge in Indian food to separate the 
# True positives from the below list

similar={
  # 'almond': 'lemon',
  # 'almonds': 'lemon',
  # 'alum powder': 'chili powder',
  # 'amaranth leaves': 'methi leaves',
  # 'amchur powder': 'chili powder',
  # 'arhar dal': 'chana dal',
  # 'atta': 'sattu',
  'baby potatoes': 'potatoes',
  # 'baingan': 'baking soda',
  # 'baking powder': 'baking soda',
  # 'banana flower': 'besan flour',
  # 'beans': 'besan',
  'beaten rice flakes': 'rice flakes',
  # 'bell pepper': 'black pepper',
  # 'bell peppers': 'black pepper',
  'bengal gram flour': 'gram flour',
  # 'besan flour': 'rice flour',
  'biryani masala': 'garam masala',
  'biryani masala powder': 'garam masala powder',
  # 'bitter gourd': 'bottle gourd',
  # 'black lentils': 'black salt',
  'black sesame seeds': 'sesame seeds',
  # 'blend rice': 'lemon juice',
  'boiled potatoes': 'potatoes',
  'brown rice': 'raw rice',
  # 'brown rice flour': 'rice flour',
  # 'canned coconut milk': 'grated coconut',
  'cardamom pods': 'cardamom',
  # 'cardamom powder': 'garam masala powder',
  'carrots': 'carrot',
  'cashews': 'cashew nuts',
  'chana daal': 'chana dal',
  'chenna': 'chhena',
  'chenna cheese': 'cottage cheese',
  'chicken chunks': 'chicken',
  'chicken thighs': 'chicken',
  # 'chickpea flour': 'rice flour',
  # 'chickpeas': 'chicken',
  'chilli': 'chillies',
  'chillies': 'green chilies',
  'cinnamon stick': 'cinnamon',
  'coconut flakes': 'coconut',
  # 'coconut ice': 'coconut',
  # 'coconut milk': 'coconut',
  # 'coconut oil': 'coconut',
  # 'corn flour': 'rice flour',
  'dates': 'dry dates',
  'desiccated coconut': 'grated coconut',
  'drumstick': 'drumsticks',
  'dry chilli': 'chillies',
  'dry coconut': 'coconut',
  'dry dates': 'dry roasted',
  'fennel': 'fennel seeds',
  # 'fennel seeds': 'sesame seeds',
  # 'fenugreek seeds': 'fennel seeds',
  'fish fillets': 'fish fillet',
  # 'fish roe': 'fish',
  # 'flour': 'rice flour',
  'fresh coconut': 'coconut',
  'fresh green chilli': 'green chilies',
  'fresh green peas': 'green peas',
  'fried milk power': 'milk powder',
  'frozen green peas': 'green peas',
  'garam masala powder': 'garam masala',
  # 'garlic powder': 'garam masala powder',
  # 'ginger powder': 'milk powder',
  # 'gram flour': 'rice flour',
  'grated coconut': 'coconut',
  # 'gravy': 'rava',
  'greek yogurt': 'yogurt',
  # 'green': 'ghee',
  # 'green beans': 'green chilies',
  'green bell pepper': 'bell pepper',
  'green cardamom': 'cardamom',
  'green chili': 'green chilies',
  'green chili paste': 'green chilies',
  'green chilli': 'green chilies',
  'green chillies': 'green chilies',
  # 'green moong beans': 'green peas',
  # 'green peas': 'green chilies',
  # 'greens': 'green peas',
  # 'gur': 'yogurt',
  'jaggery syrup': 'jaggery',
  # 'jowar flour': 'rice flour',
  # 'kala masala': 'garam masala',
  # 'lentil flour': 'wheat flour',
  'lentils': 'black lentils',
  'long beans': 'beans',
  # 'maida flour': 'rice flour',
  # 'malai': 'imli',
  # 'malvani masala': 'pav bhaji masala',
  # 'marinade': 'tamarind',
  'masala': 'garam masala',
  # 'masoor dal': 'moong dal',
  # 'mawa': 'maida',
  # 'meat curry powder': 'sambar powder',
  # 'milk powder': 'chili powder',
  'moong beans': 'moong dal',
  'mung bean': 'moong beans',
  'mushroom': 'wild mushrooms',
  'mustard': 'mustard oil',
  # 'mustard green': 'mustard oil',
  # 'mustard seed': 'mustard oil',
  # 'mustard seeds': 'mustard oil',
  # 'naan bread': 'loaf bread',
  # 'nigella seeds': 'fennel seeds',
  # 'onions': 'red onion',
  'peanut': 'peanuts',
  # 'peanut oil': 'coconut oil',
  # 'peanuts': 'nuts',
  # 'pearl onions': 'red onion',
  # 'peas': 'beans',
  # 'pigeon peas': 'green peas',
  # 'plain flour': 'rice flour',
  # 'potato': 'tomato',
  'potatoes': 'potato',
  # 'potol': 'potato',
  'raw banana': 'banana',
  'raw peanuts': 'peanuts',
  'raw rice': 'rice',
  'red chili': 'green chilies',
  'red chilli': 'green chilies',
  'red chillies': 'green chilies',
  # 'refined flour': 'rice flour',
  # 'rice flakes': 'rice flour',
  # 'ridge gourd': 'rice flour',
  'roasted gram flour': 'gram flour',
  # 'rock salt': 'black salt',
  # 'rose water': 'hot water',
  # 'sattu': 'salt',
  'sesame': 'sesame seeds',
  # 'sevai': 'sev',
  'skimmed milk powder': 'milk powder',
  'sliced almonds': 'almonds',
  # 'soaked rice': 'cooked rice',
  # 'sorghum flour': 'gram flour',
  'split pigeon peas': 'pigeon peas',
  'split urad dal': 'urad dal',
  # 'steamer': 'sesame',
  # 'sticky rice': 'basmati rice',
  # 'sweet potato': 'potato',
  'tamarind paste': 'tamarind',
  # 'tandoori masala': 'garam masala',
  # 'tea bags': 'tea leaves',
  # 'tea leaves': 'methi leaves',
  'thin rice flakes': 'rice flakes',
  # 'tomato paste': 'tomato',
  # 'tomato sauce': 'tomato',
  'tomatoes': 'tomato',
  # 'toor dal': 'moong dal',
  'vinegar': 'wine vinegar',
  'water': 'hot water',
  # 'wheat flour': 'rice flour',
  # 'white bread slices': 'white sesame seeds',
  # 'white flour': 'rice flour',
  'white sesame seeds': 'sesame seeds',
  'white urad dal': 'urad dal',
  # 'whole egg': 'whole red',
  'whole red beans': 'whole red',
  'whole urad dal': 'urad dal',
  # 'whole wheat bread': 'whole wheat flour',
  'whole wheat flour': 'wheat flour',
  # 'whole wheat rava': 'whole wheat flour',
  'yellow moong daal': 'moong dal',
  'yellow mustard': 'mustard',
  'yoghurt': 'yogurt'
}

In [38]:
# This is the final dict after filtering the above dict
# We have also hard-coded some translations of Hindi-English ingredients 
# which our Fuzzy algorithm couldn't find

similar_new={
  'baby potatoes': 'potatoes',
  'beaten rice flakes': 'rice flakes',
  'bengal gram flour': 'gram flour',
  'biryani masala': 'garam masala',
  'biryani masala powder': 'garam masala',
  'black sesame seeds': 'sesame seeds',
  'boiled potatoes': 'potatoes',
  'cardamom pods': 'cardamom',
  'carrots': 'carrot',
  'cashews': 'cashew nuts',
  'chana daal': 'chana dal',
  'chenna': 'chhena',
  'chenna cheese': 'cottage cheese',
  'chicken chunks': 'chicken',
  'chicken thighs': 'chicken',
  'chilli': 'green chillies',
  'chillies': 'green chillies',
  'cinnamon stick': 'cinnamon',
  'coconut flakes': 'coconut',
  'dry dates': 'dates',
  'desiccated coconut': 'grated coconut',
  'drumstick': 'drumsticks',
  'dry chilli': 'green chillies',
  'dry coconut': 'coconut',
  'dry roasted': 'dates',
  'fennel': 'fennel seeds',
  'fish fillets': 'fish fillet',
  'fresh coconut': 'coconut',
  'fresh green chilli': 'green chillies',
  'fresh green peas': 'green peas',
  'fried milk power': 'milk powder',
  'frozen green peas': 'green peas',
  'garam masala powder': 'garam masala',
  'grated coconut': 'coconut',
  'greek yogurt': 'yogurt',
  'green bell pepper': 'bell pepper',
  'red bell pepper': 'bell pepper',
  'yellow bell pepper': 'bell pepper',
  'green cardamom': 'cardamom',
  'green chili': 'green chillies',
  'green chili paste': 'green chillies',
  'green chilli': 'green chillies',
  'green chilies': 'green chillies',

  'gur' : 'jaggery',
  'jaggery syrup': 'jaggery',
  'lentils': 'black lentils',
  'long beans': 'beans',
  'masala': 'garam masala',
  'moong beans': 'moong dal',
  'mung bean': 'moong dal',
  'mushroom': 'wild mushrooms',
  'mustard': 'mustard oil',
  'peanut': 'peanuts',
  'potato': 'potatoes',
  'raw banana': 'banana',
  'raw peanuts': 'peanuts',
  'raw rice': 'rice',

  'red chili': 'red chillies',
  'red chilli': 'red chillies',

  'roasted gram flour': 'gram flour',
  'sesame': 'sesame seeds',
  'skimmed milk powder': 'milk powder',
  'sliced almonds': 'almonds',
  'split pigeon peas': 'pigeon peas',
  'split urad dal': 'urad dal',
  'tamarind paste': 'tamarind',
  'thin rice flakes': 'rice flakes',
  'tomato': 'tomatoes',
  'wine vinegar': 'vinegar',
  'hot water': 'water',
  'white sesame seeds': 'sesame seeds',
  'white urad dal': 'urad dal',
  'whole red': 'whole red beans',
  'whole urad dal': 'urad dal',
  'whole wheat flour': 'wheat flour',
  'yellow moong daal': 'moong dal',
  'yellow mustard': 'mustard oil',
  'yoghurt': 'yogurt',
  'dahi': 'yogurt',
  'palak' : 'spinach',
  'aloo' : 'potatoes',
  'badam' : 'peanuts',
  'baingan' : 'eggplant',
  'brinjal' : 'eggplant',
  'tomato sauce' : 'sauce'
}

In [39]:
# Using the above dict to map common ingredients into a new_ingredients_dict

new_ing_dic = collections.defaultdict(int)

for f in food.index:
    tmp_list = food.at[f, 'Ingredients'].split(', ')
    for i in tmp_list:
        i = i.lower().strip()
        if i in similar_new:
            i = similar_new[i]
        new_ing_dic[i] += 1
            
new_ing_df = pd.DataFrame.from_dict(new_ing_dic, orient='index')\
    .rename(columns={0:'count'})
new_ing_df.sort_index().loc['red':'red0'].T

red chillies  red food coloring  red kidney beans  red onion
count             6                  1                 2          3

In [40]:
BoI_df = pd.DataFrame(
    np.zeros(len(food)*len(new_ing_dic)).reshape(len(food),len(new_ing_dic))\
    .astype(int),index=food.index, columns=new_ing_df.index)

for f in food.index:
    tmp_list = food.at[f, 'Ingredients'].split(', ')
    for i in tmp_list:
        i = i.lower()
        if i[0] == ' ':
            i = i[1:]
        if i[-1] ==' ':
            i = i[:-1]
        if i in similar:
            i = similar[i]
        BoI_df.at[f, i]=1

In [41]:
# Our string matching routine has reduced the ingredients size form 350s to 240s
# heavily bringing down the redudancy
BoI_df=BoI_df.dropna(axis=1)
BoI_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 241 entries, 0 to 240
Columns: 270 entries, maida flour to ginger powder
dtypes: int64(270)
memory usage: 508.5 KB


In [43]:
# Bag of Ingredients

BoI_df.head()

maida flour  yogurt  oil  sugar  gram flour  ghee  carrot  milk  \
0            1       1    1      1           0     0       0     0   
1            0       0    0      1           1     1       0     0   
2            0       0    0      1           0     1       1     1   
3            0       0    0      1           0     1       0     1   
4            0       0    0      1           0     1       0     1   

   cashew nuts  raisins  flour  kewra  clarified butter  almonds  pistachio  \
0            0        0      0      0                 0        0          0   
1            0        0      0      0                 0        0          0   
2            1        1      0      0                 0        0          0   
3            0        0      1      1                 1        1          1   
4            0        0      0      0                 0        0          0   

   saffron  cardamom  milk powder  plain flour  baking powder  water  \
0        0         0            0            0              0      0   
1        0         0            0            0              0      0   
2        0         0            0            0              0      0   
3        1         1            0            0              0      0   
4        0         0            1            1              1      0   

   rose water  sugar syrup  lentil flour  maida  corn flour  baking soda  \
0           0            0             0      0           0            0   
1           0            0             0      0           0            0   
2           0            0             0      0           0            0   
3           0            0             0      0           0            0   
4           1            0             0      0           0            0   

   vinegar  curd  turmeric  cottage cheese  nuts  firm white pumpkin  \
0        0     0         0               0     0                   0   
1        0     0         0               0     0                   0   
2        0     0         0               0     0                   0   
3        0     0         0               0     0                   0   
4        0     0         0               0     0                   0   

   kitchen lime  alum powder  rice  condensed milk  spices  semolina  khoa  \
0             0            0     0               0       0         0     0   
1             0            0     0               0       0         0     0   
2             0            0     0               0       0         0     0   
3             0            0     0               0       0         0     0   
4             0            0     0               0       0         0     0   

   coconut  molu leaf  dry fruits  chhena  cream  lemon juice  refined flour  \
0        0          0           0       0      0            0              0   
1        0          0           0       0      0            0              0   
2        0          0           0       0      0            0              0   
3        0          0           0       0      0            0              0   
4        0          0           0       0      0            0              0   

   fennel seeds  besan flour  jaggery  rice flour  wheat flour  \
0             0            0        0           0            0   
1             0            0        0           0            0   
2             0            0        0           0            0   
3             0            0        0           0            0   
4             0            0        0           0            0   

   sweetened milk  reduced milk  vegetable oil  elachi  besan  \
0               0             0              0       0      0   
1               0             0              0       0      0   
2               0             0              0       0      0   
3               0             0              0       0      0   
4               0             0              0       0      0   

   cardamom powder  cashews and raisins  peanu

In [44]:
# Performing PCA on the bag of ingredients for better feature selection

from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn import metrics

pca = PCA(0.90)
pca = pca.fit(BoI_df)
pca.n_components_

99

In [ ]:
ing_column_names = []
for i in range(np.shape(pca.transform(BoI_df))[1]):
  ing_column_names.append('ing'+ str(i))



In [ ]:
tempdf = pd.DataFrame(pca.transform(BoI_df), columns = ing_column_names)
data.shape

(241, 9)

In [ ]:
final_data = pd.concat([data,tempdf],axis=1)
final_data

Ingredients            Diet  \
0                      Maida flour, yogurt, oil, sugar      vegetarian   
1                              Gram flour, ghee, sugar      vegetarian   
2         Carrots, milk, sugar, ghee, cashews, raisins      vegetarian   
3    Flour, ghee, kewra, milk, clarified butter, su...      vegetarian   
4    Milk powder, plain flour, baking powder, ghee,...      vegetarian   
5                            Sugar syrup, lentil flour      vegetarian   
6    Maida, corn flour, baking soda, vinegar, curd,...      vegetarian   
7                          Milk, cottage cheese, sugar      vegetarian   
8                            Yogurt, milk, nuts, sugar      vegetarian   
9    Firm white pumpkin, sugar, kitchen lime, alum ...      vegetarian   
10                                   Rice, sugar, nuts      vegetarian   
11                 Condensed milk, sugar, spices, nuts      vegetarian   
12                          Semolina, ghee, nuts, milk      vegetarian   
13                            Khoa, coconut, molu leaf      vegetarian   
14                        Corn flour, ghee, dry fruits      vegetarian   
15             Gram flour, ghee, sugar, milk, cardamom      vegetarian   
16                                 Chhena, sugar, ghee      vegetarian   
17                                 Chhena, sugar, milk      vegetarian   
18                                Sugar, chenna cheese      vegetarian   
19   Flour, cream, sugar, saffron, lemon juice, coc...      vegetarian   
20    Chenna, condensed milk, sugar, saffron, cardamom      vegetarian   
21                                 Chhena, sugar, ghee      vegetarian   
22                Flour, fried milk power, sugar syrup      vegetarian   
23          Yoghurt, refined flour, ghee, fennel seeds      vegetarian   
24                            Besan flour, sugar, ghee      vegetarian   
25                                       Milk, jaggery      vegetarian   
26                          Chhena, sugar, ghee, flour      vegetarian   
27                             Rice flour, wheat flour      vegetarian   
28                              Chenna, sweetened milk      vegetarian   
29                     Chhena, reduced milk, pistachio      vegetarian   
30                             Chhena, sugar, cardamom      vegetarian   
31                      Milk, sugar, saffron, cardamom      vegetarian   
32    Rice flour, jaggery, ghee, vegetable oil, elachi      vegetarian   
33                           Rice flour, jaggery, ghee      vegetarian   
34   Besan, jaggery, cardamom powder, ghee, cashews...      vegetarian   
35                                    Peanuts, jaggery      vegetarian   
36                  Milk, Sugar, Dharwadi buffalo milk      vegetarian   
37                                    Loaf bread, milk      vegetarian   
38             Rice flour, sugar, salt, ghee, semolina      vegetarian   
39                                  Wheat flour, sugar      vegetarian   
40                                 Black lentils, rice      vegetarian   
41   Besan flour, semolina, mung bean, jaggery, coc...      vegetarian   
42   Maida flour, turmeric, coconut, chickpeas, jag...      vegetarian   
43                                    Rice flour, milk      vegetarian   
44                                  Chana dal, jaggery      vegetarian   
45                        Rice, jaggery, cashews, ghee      vegetarian   
46                    Rice flour, powdered sugar, ghee      vegetarian   
47                               Apricots, sugar syrup      vegetarian   
48                            Vermicelli pudding, milk      vegetarian   
49                Rice flour, banana, jaggery, coconut      vegetarian   
50                        Rice flour, jaggery, coconut      vegetarian   
51                Rice flour, jaggery, khus-khus seeds      vegetarian   
52                                   Sugar, milk, nuts      vegetarian   
53                                      Cucumbe

In [ ]:
final_data.shape

(241, 108)

In [ ]:
pakka_final_data=final_data.drop(columns=["Ingredients"])

In [ ]:
pakka_final_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 241 entries, 0 to 240
Columns: 107 entries, Diet to ing98
dtypes: float64(102), int64(1), object(4)
memory usage: 201.6+ KB


In [ ]:
df = pakka_final_data.copy()

In [ ]:
df.head()

Diet  Preparation Time  Cooking Time Flavor   Course Region  \
0  vegetarian              45.0          25.0  sweet  dessert   East   
1  vegetarian              80.0          30.0  sweet  dessert   West   
2  vegetarian              15.0          60.0  sweet  dessert  North   
3  vegetarian              15.0          30.0  sweet  dessert   West   
4  vegetarian              15.0          40.0  sweet  dessert   East   

   Price/unit  Total      ing0      ing1      ing2      ing3      ing4  \
0         260   70.0  0.638262 -0.214640  0.153183  0.055685 -0.095383   
1         270  110.0  0.881877 -0.151533  0.030913  0.303766 -0.243389   
2         450   75.0  1.284324 -0.509263  0.256137 -0.073878  0.241311   
3         460   45.0  1.687540 -0.511026  0.349767  0.171247  0.058408   
4         300   55.0  1.339249 -0.369189  0.226180  0.001485  0.036164   

       ing5      ing6      ing7      ing8      ing9     ing10     ing11  \
0  0.109502  0.056338 -0.172120 -0.045739 -0.291777 -0.401254 -0.190111   
1  0.446090 -0.190131  0.681535  0.232293 -0.177573 -0.453553  0.196953   
2  0.064336 -0.105748  0.199021 -0.023972  0.493316 -0.455705 -0.131237   
3  0.131535 -0.117514  0.066387 -0.008135  0.163714  0.875769  0.880653   
4  0.058416 -0.153069  0.379087  0.193676  0.240415 -0.175163 -0.068755   

      ing12     ing13     ing14     ing15     ing16     ing17     ing18  \
0  0.325834 -0.665878  0.152685 -0.103096  0.589214  0.068718  0.027374   
1  0.019965 -0.045817 -0.155692 -0.094780 -0.148790 -0.200539 -0.129675   
2 -0.225831  0.483020  0.319040 -0.130005 -0.234901  0.183425  0.260781   
3  0.522569  0.909907  0.512765  0.631619  0.265113 -0.056764 -0.128931   
4 -0.066537  0.213048  0.287509  0.645319 -0.279181  0.025023  0.475251   

      ing19     ing20     ing21     ing22     ing23     ing24     ing25  \
0 -0.158451 -0.091949 -0.109814 -0.100765  0.090086 -0.132264 -0.256061   
1  0.133476  0.200948  0.048094  0.009741  0.073621  0.086193  0.022871   
2  0.499051  0.095162  0.540733 -0.015536 -0.187604  0.506257 -0.398080   
3 -0.054555 -0.210422 -0.229879  0.194242  0.259898  0.183209  0.108469   
4  0.172541 -0.003310  0.137398  0.112972 -0.168448 -0.253074 -0.020511   

      ing26     ing27     ing28     ing29     ing30     ing31     ing32  \
0 -0.251836  0.061117  0.085380  0.203848 -0.122534  0.002543 -0.148836   
1  0.034778  0.031636 -0.046646 -0.059543 -0.068608 -0.033690  0.110615   
2 -0.113124  0.081358  0.051172 -0.253062 -0.375070  0.114482 -0.151100   
3 -0.394997  0.038273 -0.528973 -0.179255 -0.336710  0.226097 -0.043067   
4  0.313288 -0.117297 -0.154472 -0.078339 -0.248462  0.024267  0.276870   

      ing33     ing34     ing35     ing36     ing37     ing38     ing39  \
0  0.150874 -0.015653  0.097574  0.086173  0.237091  0.121351  0.008438   
1  0.054953  0.011730 -0.046603 -0.037033 -0.022259 -0.015880 -0.065793   
2 -0.026684 -0.435271  0.160915 -0.258727  0.062935  0.204997  0.203494   
3 -0.186019  0.236464 -0.200378  0.099906  0.089467  0.016693 -0.177384   
4 -0.152716  0.796444  0.390161  0.139504  0.054825  0.021457  0.317878   

      ing40     ing41     ing42     ing43     ing44     ing45     ing46  \
0  0.095851 -0.091992  0.015456 -0.002107  0.046461  0.171435  0.026029   
1 -0.074958 -0.044879 -0.206343  0.082325  0.107145 -0.060108 -0.020059   
2  0.300927 -0.222635 -0.029380 -0.024700 -0.109397  0.061773 -0.013300   
3 -0.219394 -0.229803 -0.063303 -0.054017 -0.074842 -0.378132 -0.132878   
4  0.256998  0.384468  0.022148  0.060141  0.699756  0.623130 -0.042418   

      ing47     ing48     ing49     ing50     ing51     ing52     ing53  \
0 -0.168113 -0.126655  0.086241  0.041887  0.264038 -0.247458 -0.122325   
1 -0.034177 -0.055133  0.005742 -0.062372 -0.014028 -0.051468 -0.060694   
2 -0.183628  0.045600  0.012343 -0.009856 -0.003939 -0.101397  0.014895   
3 -0.073071  0.049145  0.358076  0.033198  0.274765  0.086178  0.161975   
4  0.054619 -0.001780 -0.411904  0.079452 -0.07027

In [ ]:
df

Diet  Preparation Time  Cooking Time  Flavor  Course  \
0        vegetarian              45.0          25.0   sweet       0   
1        vegetarian              80.0          30.0   sweet       0   
2        vegetarian              15.0          60.0   sweet       0   
3        vegetarian              15.0          30.0   sweet       0   
4        vegetarian              15.0          40.0   sweet       0   
5        vegetarian              10.0          50.0   sweet       0   
6        vegetarian              10.0          50.0   sweet       0   
7        vegetarian              20.0          30.0   sweet       0   
8        vegetarian               5.0           5.0   sweet       0   
9        vegetarian              10.0          30.0   sweet       0   
10       vegetarian              30.0          20.0   sweet       0   
11       vegetarian              10.0          45.0   sweet       0   
12       vegetarian              10.0          25.0   sweet       0   
13       vegetarian              10.0          20.0   sweet       0   
14       vegetarian              10.0          60.0   sweet       0   
15       vegetarian              10.0          60.0   sweet       0   
16       vegetarian              10.0          50.0   sweet       0   
17       vegetarian              20.0          60.0   sweet       0   
18       vegetarian              10.0          45.0   sweet       0   
19       vegetarian              40.0          60.0   sweet       0   
20       vegetarian              25.0          60.0   sweet       0   
21       vegetarian              45.0          45.0   sweet       0   
22       vegetarian              20.0          30.0   sweet       0   
23       vegetarian              10.0         120.0   sweet       0   
24       vegetarian              15.0          30.0   sweet       0   
25       vegetarian             480.0          30.0   sweet       0   
26       vegetarian              45.0          45.0   sweet       0   
27       vegetarian              15.0          35.0   sweet       0   
28       vegetarian              15.0          30.0   sweet       0   
29       vegetarian             180.0          60.0   sweet       0   
30       vegetarian              10.0          90.0   sweet       0   
31       vegetarian              30.0          20.0   sweet       0   
32       vegetarian              10.0          50.0   sweet       0   
33       vegetarian              15.0          75.0   sweet       0   
34       vegetarian               5.0          35.0   sweet       0   
35       vegetarian              10.0          20.0   sweet       0   
36       vegetarian              20.0          60.0   sweet       0   
37       vegetarian              20.0          30.0   sweet       0   
38       vegetarian              10.0          30.0   sweet       0   
39       vegetarian              10.0          30.0   sweet       0   
40       vegetarian              10.0          20.0   sweet       0   
41       vegetarian               5.0          20.0   sweet       0   
42       vegetarian             180.0          60.0   sweet       1   
43       vegetarian              10.0          25.0   sweet       0   
44       vegetarian             240.0          60.0   sweet       0   
45       vegetarian               5.0          20.0   sweet       0   
46       vegetarian              10.0          60.0   sweet       0   
47       vegetarian              10.0          20.0   sweet       0   
48       vegetarian              10.0          20.0   sweet       0   
49       vegetarian              10.0          20.0   sweet       0   
50       vegetarian              40.0          15.0   sweet       0   
51       vegetarian              10.0          50.0   sweet       0   
52       vegetarian              10.0          35.0   sweet       0   
53       vegetarian              10.0          50.0   sweet       0   
54       vegetarian              10.0          60.0   sweet       0   
55       vegetarian              10.0  

In [ ]:
pd.unique(df['Course'])

array(['dessert', 'main course', 'starter', 'snack'], dtype=object)

In [ ]:
#Creating the dependent variable class
factor = pd.factorize(df['Course'])
df.Course = factor[0]
definitions = factor[1]
print(df.Course.head())
print(definitions)

0    0
1    0
2    0
3    0
4    0
Name: Course, dtype: int64
Index(['dessert', 'main course', 'starter', 'snack'], dtype='object')


In [ ]:
df

Diet  Preparation Time  Cooking Time  Flavor  Course  \
0        vegetarian              45.0          25.0   sweet       0   
1        vegetarian              80.0          30.0   sweet       0   
2        vegetarian              15.0          60.0   sweet       0   
3        vegetarian              15.0          30.0   sweet       0   
4        vegetarian              15.0          40.0   sweet       0   
5        vegetarian              10.0          50.0   sweet       0   
6        vegetarian              10.0          50.0   sweet       0   
7        vegetarian              20.0          30.0   sweet       0   
8        vegetarian               5.0           5.0   sweet       0   
9        vegetarian              10.0          30.0   sweet       0   
10       vegetarian              30.0          20.0   sweet       0   
11       vegetarian              10.0          45.0   sweet       0   
12       vegetarian              10.0          25.0   sweet       0   
13       vegetarian              10.0          20.0   sweet       0   
14       vegetarian              10.0          60.0   sweet       0   
15       vegetarian              10.0          60.0   sweet       0   
16       vegetarian              10.0          50.0   sweet       0   
17       vegetarian              20.0          60.0   sweet       0   
18       vegetarian              10.0          45.0   sweet       0   
19       vegetarian              40.0          60.0   sweet       0   
20       vegetarian              25.0          60.0   sweet       0   
21       vegetarian              45.0          45.0   sweet       0   
22       vegetarian              20.0          30.0   sweet       0   
23       vegetarian              10.0         120.0   sweet       0   
24       vegetarian              15.0          30.0   sweet       0   
25       vegetarian             480.0          30.0   sweet       0   
26       vegetarian              45.0          45.0   sweet       0   
27       vegetarian              15.0          35.0   sweet       0   
28       vegetarian              15.0          30.0   sweet       0   
29       vegetarian             180.0          60.0   sweet       0   
30       vegetarian              10.0          90.0   sweet       0   
31       vegetarian              30.0          20.0   sweet       0   
32       vegetarian              10.0          50.0   sweet       0   
33       vegetarian              15.0          75.0   sweet       0   
34       vegetarian               5.0          35.0   sweet       0   
35       vegetarian              10.0          20.0   sweet       0   
36       vegetarian              20.0          60.0   sweet       0   
37       vegetarian              20.0          30.0   sweet       0   
38       vegetarian              10.0          30.0   sweet       0   
39       vegetarian              10.0          30.0   sweet       0   
40       vegetarian              10.0          20.0   sweet       0   
41       vegetarian               5.0          20.0   sweet       0   
42       vegetarian             180.0          60.0   sweet       1   
43       vegetarian              10.0          25.0   sweet       0   
44       vegetarian             240.0          60.0   sweet       0   
45       vegetarian               5.0          20.0   sweet       0   
46       vegetarian              10.0          60.0   sweet       0   
47       vegetarian              10.0          20.0   sweet       0   
48       vegetarian              10.0          20.0   sweet       0   
49       vegetarian              10.0          20.0   sweet       0   
50       vegetarian              40.0          15.0   sweet       0   
51       vegetarian              10.0          50.0   sweet       0   
52       vegetarian              10.0          35.0   sweet       0   
53       vegetarian              10.0          50.0   sweet       0   
54       vegetarian              10.0          60.0   sweet       0   
55       vegetarian              10.0  

In [ ]:
ax = df.copy()
ax

Diet  Preparation Time  Cooking Time  Flavor  Course  \
0        vegetarian              45.0          25.0   sweet       0   
1        vegetarian              80.0          30.0   sweet       0   
2        vegetarian              15.0          60.0   sweet       0   
3        vegetarian              15.0          30.0   sweet       0   
4        vegetarian              15.0          40.0   sweet       0   
5        vegetarian              10.0          50.0   sweet       0   
6        vegetarian              10.0          50.0   sweet       0   
7        vegetarian              20.0          30.0   sweet       0   
8        vegetarian               5.0           5.0   sweet       0   
9        vegetarian              10.0          30.0   sweet       0   
10       vegetarian              30.0          20.0   sweet       0   
11       vegetarian              10.0          45.0   sweet       0   
12       vegetarian              10.0          25.0   sweet       0   
13       vegetarian              10.0          20.0   sweet       0   
14       vegetarian              10.0          60.0   sweet       0   
15       vegetarian              10.0          60.0   sweet       0   
16       vegetarian              10.0          50.0   sweet       0   
17       vegetarian              20.0          60.0   sweet       0   
18       vegetarian              10.0          45.0   sweet       0   
19       vegetarian              40.0          60.0   sweet       0   
20       vegetarian              25.0          60.0   sweet       0   
21       vegetarian              45.0          45.0   sweet       0   
22       vegetarian              20.0          30.0   sweet       0   
23       vegetarian              10.0         120.0   sweet       0   
24       vegetarian              15.0          30.0   sweet       0   
25       vegetarian             480.0          30.0   sweet       0   
26       vegetarian              45.0          45.0   sweet       0   
27       vegetarian              15.0          35.0   sweet       0   
28       vegetarian              15.0          30.0   sweet       0   
29       vegetarian             180.0          60.0   sweet       0   
30       vegetarian              10.0          90.0   sweet       0   
31       vegetarian              30.0          20.0   sweet       0   
32       vegetarian              10.0          50.0   sweet       0   
33       vegetarian              15.0          75.0   sweet       0   
34       vegetarian               5.0          35.0   sweet       0   
35       vegetarian              10.0          20.0   sweet       0   
36       vegetarian              20.0          60.0   sweet       0   
37       vegetarian              20.0          30.0   sweet       0   
38       vegetarian              10.0          30.0   sweet       0   
39       vegetarian              10.0          30.0   sweet       0   
40       vegetarian              10.0          20.0   sweet       0   
41       vegetarian               5.0          20.0   sweet       0   
42       vegetarian             180.0          60.0   sweet       1   
43       vegetarian              10.0          25.0   sweet       0   
44       vegetarian             240.0          60.0   sweet       0   
45       vegetarian               5.0          20.0   sweet       0   
46       vegetarian              10.0          60.0   sweet       0   
47       vegetarian              10.0          20.0   sweet       0   
48       vegetarian              10.0          20.0   sweet       0   
49       vegetarian              10.0          20.0   sweet       0   
50       vegetarian              40.0          15.0   sweet       0   
51       vegetarian              10.0          50.0   sweet       0   
52       vegetarian              10.0          35.0   sweet       0   
53       vegetarian              10.0          50.0   sweet       0   
54       vegetarian              10.0          60.0   sweet       0   
55       vegetarian              10.0  

In [ ]:
del ax['Course']
ax

Diet  Preparation Time  Cooking Time  Flavor      Region  \
0        vegetarian              45.0          25.0   sweet        East   
1        vegetarian              80.0          30.0   sweet        West   
2        vegetarian              15.0          60.0   sweet       North   
3        vegetarian              15.0          30.0   sweet        West   
4        vegetarian              15.0          40.0   sweet        East   
5        vegetarian              10.0          50.0   sweet        East   
6        vegetarian              10.0          50.0   sweet       North   
7        vegetarian              20.0          30.0   sweet        East   
8        vegetarian               5.0           5.0   sweet       North   
9        vegetarian              10.0          30.0   sweet       North   
10       vegetarian              30.0          20.0   sweet        East   
11       vegetarian              10.0          45.0   sweet       North   
12       vegetarian              10.0          25.0   sweet        West   
13       vegetarian              10.0          20.0   sweet       North   
14       vegetarian              10.0          60.0   sweet       North   
15       vegetarian              10.0          60.0   sweet        West   
16       vegetarian              10.0          50.0   sweet        East   
17       vegetarian              20.0          60.0   sweet        East   
18       vegetarian              10.0          45.0   sweet        East   
19       vegetarian              40.0          60.0   sweet        East   
20       vegetarian              25.0          60.0   sweet        East   
21       vegetarian              45.0          45.0   sweet        East   
22       vegetarian              20.0          30.0   sweet  North East   
23       vegetarian              10.0         120.0   sweet       North   
24       vegetarian              15.0          30.0   sweet        East   
25       vegetarian             480.0          30.0   sweet        East   
26       vegetarian              45.0          45.0   sweet        East   
27       vegetarian              15.0          35.0   sweet  North East   
28       vegetarian              15.0          30.0   sweet        East   
29       vegetarian             180.0          60.0   sweet        East   
30       vegetarian              10.0          90.0   sweet        East   
31       vegetarian              30.0          20.0   sweet        East   
32       vegetarian              10.0          50.0   sweet        East   
33       vegetarian              15.0          75.0   sweet       South   
34       vegetarian               5.0          35.0   sweet       South   
35       vegetarian              10.0          20.0   sweet        West   
36       vegetarian              20.0          60.0   sweet       South   
37       vegetarian              20.0          30.0   sweet       South   
38       vegetarian              10.0          30.0   sweet       South   
39       vegetarian              10.0          30.0   sweet       South   
40       vegetarian              10.0          20.0   sweet       South   
41       vegetarian               5.0          20.0   sweet       South   
42       vegetarian             180.0          60.0   sweet       South   
43       vegetarian              10.0          25.0   sweet       South   
44       vegetarian             240.0          60.0   sweet       South   
45       vegetarian               5.0          20.0   sweet       South   
46       vegetarian              10.0          60.0   sweet       South   
47       vegetarian              10.0          20.0   sweet       South   
48       vegetarian              10.0          20.0   sweet       South   
49       vegetarian              10.0          20.0   sweet       South   
50       vegetarian              40.0          15.0   sweet       South   
51       vegetarian              10.0          50.0   sweet        West   
52       vegetarian              10.0   

In [ ]:
cat_col = ['Diet', 'Flavor', 'Region']
ax = pd.get_dummies(ax, columns = cat_col)
ax.head()

Preparation Time  Cooking Time  Price/unit  Total      ing0      ing1  \
0              45.0          25.0         260   70.0  0.638262 -0.214640   
1              80.0          30.0         270  110.0  0.881877 -0.151533   
2              15.0          60.0         450   75.0  1.284324 -0.509263   
3              15.0          30.0         460   45.0  1.687540 -0.511026   
4              15.0          40.0         300   55.0  1.339249 -0.369189   

       ing2      ing3      ing4      ing5      ing6      ing7      ing8  \
0  0.153183  0.055685 -0.095383  0.109502  0.056338 -0.172120 -0.045739   
1  0.030913  0.303766 -0.243389  0.446090 -0.190131  0.681535  0.232293   
2  0.256137 -0.073878  0.241311  0.064336 -0.105748  0.199021 -0.023972   
3  0.349767  0.171247  0.058408  0.131535 -0.117514  0.066387 -0.008135   
4  0.226180  0.001485  0.036164  0.058416 -0.153069  0.379087  0.193676   

       ing9     ing10     ing11     ing12     ing13     ing14     ing15  \
0 -0.291777 -0.401254 -0.190111  0.325834 -0.665878  0.152685 -0.103096   
1 -0.177573 -0.453553  0.196953  0.019965 -0.045817 -0.155692 -0.094780   
2  0.493316 -0.455705 -0.131237 -0.225831  0.483020  0.319040 -0.130005   
3  0.163714  0.875769  0.880653  0.522569  0.909907  0.512765  0.631619   
4  0.240415 -0.175163 -0.068755 -0.066537  0.213048  0.287509  0.645319   

      ing16     ing17     ing18     ing19     ing20     ing21     ing22  \
0  0.589214  0.068718  0.027374 -0.158451 -0.091949 -0.109814 -0.100765   
1 -0.148790 -0.200539 -0.129675  0.133476  0.200948  0.048094  0.009741   
2 -0.234901  0.183425  0.260781  0.499051  0.095162  0.540733 -0.015536   
3  0.265113 -0.056764 -0.128931 -0.054555 -0.210422 -0.229879  0.194242   
4 -0.279181  0.025023  0.475251  0.172541 -0.003310  0.137398  0.112972   

      ing23     ing24     ing25     ing26     ing27     ing28     ing29  \
0  0.090086 -0.132264 -0.256061 -0.251836  0.061117  0.085380  0.203848   
1  0.073621  0.086193  0.022871  0.034778  0.031636 -0.046646 -0.059543   
2 -0.187604  0.506257 -0.398080 -0.113124  0.081358  0.051172 -0.253062   
3  0.259898  0.183209  0.108469 -0.394997  0.038273 -0.528973 -0.179255   
4 -0.168448 -0.253074 -0.020511  0.313288 -0.117297 -0.154472 -0.078339   

      ing30     ing31     ing32     ing33     ing34     ing35     ing36  \
0 -0.122534  0.002543 -0.148836  0.150874 -0.015653  0.097574  0.086173   
1 -0.068608 -0.033690  0.110615  0.054953  0.011730 -0.046603 -0.037033   
2 -0.375070  0.114482 -0.151100 -0.026684 -0.435271  0.160915 -0.258727   
3 -0.336710  0.226097 -0.043067 -0.186019  0.236464 -0.200378  0.099906   
4 -0.248462  0.024267  0.276870 -0.152716  0.796444  0.390161  0.139504   

      ing37     ing38     ing39     ing40     ing41     ing42     ing43  \
0  0.237091  0.121351  0.008438  0.095851 -0.091992  0.015456 -0.002107   
1 -0.022259 -0.015880 -0.065793 -0.074958 -0.044879 -0.206343  0.082325   
2  0.062935  0.204997  0.203494  0.300927 -0.222635 -0.029380 -0.024700   
3  0.089467  0.016693 -0.177384 -0.219394 -0.229803 -0.063303 -0.054017   
4  0.054825  0.021457  0.317878  0.256998  0.384468  0.022148  0.060141   

      ing44     ing45     ing46     ing47     ing48     ing49     ing50  \
0  0.046461  0.171435  0.026029 -0.168113 -0.126655  0.086241  0.041887   
1  0.107145 -0.060108 -0.020059 -0.034177 -0.055133  0.005742 -0.062372   
2 -0.109397  0.061773 -0.013300 -0.183628  0.045600  0.012343 -0.009856   
3 -0.074842 -0.378132 -0.132878 -0.073071  0.049145  0.358076  0.033198   
4  0.699756  0.623130 -0.042418  0.054619 -0.001780 -0.411904  0.079452   

      ing51     ing52     ing53     ing54     ing55     ing56     ing57  \
0  0.264038 -0.247458 -0.122325  0.167794  0.082744  0.327911  0.436604   
1 -0.014028 -0.051468 -0.060694  0.057988 -0.003410 -0.028612 -0.003566   
2 -0.003939 -0.101397  0.014895  0.018038  0.028091  0.055590 -0.044323   
3  0.274765  0.086178  0.161975 -0.271053 -0.118060  0.163781 -0.098365   
4 -0.070276 -0

In [ ]:
ax.shape

(241, 115)

In [ ]:
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test=train_test_split(ax, df['Course'], test_size=0.20, random_state=7, shuffle=True)

In [ ]:
# Feature Scaling
scaler = StandardScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

In [ ]:
y_train

66     1
180    3
210    1
77     2
96     1
13     0
97     1
9      0
18     0
199    1
228    1
140    3
31     0
115    1
70     1
226    1
222    1
14     0
40     0
45     0
223    1
32     0
141    1
178    1
154    1
28     0
63     1
114    1
224    1
15     0
125    1
58     0
184    1
36     0
111    1
203    3
215    1
51     0
200    3
165    1
90     1
85     3
161    3
216    1
234    1
91     1
139    1
158    0
239    0
164    1
37     0
170    0
116    1
177    1
202    3
134    1
49     0
133    3
5      0
17     0
113    3
102    1
207    0
147    1
106    1
162    3
201    3
104    1
214    1
153    1
98     1
86     3
62     0
64     1
26     0
132    1
41     0
105    1
52     0
240    0
236    0
117    3
150    3
29     0
79     1
131    1
39     0
138    0
54     0
43     0
169    3
48     0
205    3
59     0
53     0
20     0
124    1
231    1
227    1
156    1
76     1
197    1
107    1
187    3
12     0
16     0
47     0
173    3
119    3
21     0
146    1
1

In [ ]:
pd.unique(y_train)

array([1, 3, 2, 0])

In [ ]:
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier

forest = RandomForestClassifier(random_state = 1)

n_estimators = [100, 300, 500, 800, 1200]
max_depth = [5, 8, 15, 25, 30]
min_samples_split = [2, 5, 10, 15, 100]
min_samples_leaf = [1, 2, 5, 10] 

hyperF = dict(n_estimators = n_estimators, max_depth = max_depth,  
              min_samples_split = min_samples_split, 
             min_samples_leaf = min_samples_leaf)

gridF = GridSearchCV(forest, hyperF, cv = 3, verbose = 1, 
                      n_jobs = -1)
bestF = gridF.fit(x_train, y_train)

Fitting 3 folds for each of 500 candidates, totalling 1500 fits


/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 2 members, which is less than n_splits=3.
  % (min_groups, self.n_splits)), UserWarning)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:   37.6s
[Parallel(n_jobs=-1)]: Done 196 tasks      | elapsed:  2.6min
[Parallel(n_jobs=-1)]: Done 446 tasks      | elapsed:  5.8min
[Parallel(n_jobs=-1)]: Done 796 tasks      | elapsed: 10.4min
[Parallel(n_jobs=-1)]: Done 1246 tasks      | elapsed: 16.3min
[Parallel(n_jobs=-1)]: Done 1500 out of 1500 | elapsed: 19.7min finished


In [ ]:
bestF.best_params_

{'max_depth': 8,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 100}

In [ ]:
rfc = RandomForestClassifier(random_state = 1, max_depth = 8, n_estimators = 100, min_samples_split = 2, min_samples_leaf = 1)
                                   
model = rfc.fit(x_train, y_train)
y_pred = model.predict(x_test)

In [ ]:
from sklearn.metrics import f1_score

f1_score(y_test, y_pred, average='micro')

0.8571428571428571

In [ ]:
from sklearn.metrics import plot_confusion_matrix
from sklearn.metrics import confusion_matrix

cnf_matrix = confusion_matrix(y_test, y_pred)
print(cnf_matrix)

[[15  0  0]
 [ 0 27  0]
 [ 1  6  0]]


In [ ]:
from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))


ValueError: ignored

In [ ]:
# Predicting the Test set results
#Reverse factorize (converting y_pred from 0s,1s and 2s to Iris-setosa, Iris-versicolor and Iris-virginica
reversefactor = dict(zip(range(4),definitions))
y_test1 = np.vectorize(reversefactor.get)(y_test)
y_pred = np.vectorize(reversefactor.get)(y_pred)
# Making the Confusion Matrix
print(pd.crosstab(y_test1, y_pred, rownames=['Actual'], colnames=['Predicted']))

Predicted    dessert  main course
Actual                           
dessert           15            0
main course        0           27
snack              1            6


In [ ]:
# Linear SVM
from sklearn.svm import SVC
svclassifier = SVC(kernel='linear')
svclassifier.fit(x_train, y_train)

y_svm1 = svclassifier.predict(x_test)

from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test,y_svm1))
print(classification_report(y_test,y_svm1))
print(f1_score(y_test, y_svm1, average='micro'))

[[14  1  0]
 [ 5 18  4]
 [ 1  4  2]]
              precision    recall  f1-score   support

           0       0.70      0.93      0.80        15
           1       0.78      0.67      0.72        27
           3       0.33      0.29      0.31         7

    accuracy                           0.69        49
   macro avg       0.61      0.63      0.61        49
weighted avg       0.69      0.69      0.69        49

0.6938775510204082


In [ ]:
# Polynomial kernel
from sklearn.svm import SVC
svclassifier1 = SVC(kernel='poly', degree=8)
svclassifier1.fit(x_train, y_train)

y_svm2 = svclassifier1.predict(x_test)

from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test, y_svm2))
print(classification_report(y_test, y_svm2))
print(f1_score(y_test, y_svm2, average='micro'))

[[ 0 15  0]
 [ 0 27  0]
 [ 0  7  0]]
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        15
           1       0.55      1.00      0.71        27
           3       0.00      0.00      0.00         7

    accuracy                           0.55        49
   macro avg       0.18      0.33      0.24        49
weighted avg       0.30      0.55      0.39        49

0.5510204081632653


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [ ]:
# Gaussian Kernel

from sklearn.model_selection import GridSearchCV 
from sklearn.svm import SVC



# defining parameter range 
param_grid = {'C': [0.1, 1, 10, 100, 1000],  
              'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
              'kernel': ['rbf']}  
  
grid = GridSearchCV(SVC(), param_grid, refit = True, verbose = 3) 
  
# fitting the model for grid search 
grid.fit(x_train, y_train)

Fitting 5 folds for each of 25 candidates, totalling 125 fits
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.526, total=   0.0s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.500, total=   0.0s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.500, total=   0.0s
[CV] C=0.1, gamma=0.1, kernel=rbf ....................................
[CV] ........ C=0.1, gamma=0.1, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=0.1, kernel=rbf ....................................
[CV] ........ C

/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 2 members, which is less than n_splits=5.
  % (min_groups, self.n_splits)), UserWarning)
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


[CV] ....... C=0.1, gamma=0.01, kernel=rbf, score=0.500, total=   0.0s
[CV] C=0.1, gamma=0.001, kernel=rbf ..................................
[CV] ...... C=0.1, gamma=0.001, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=0.001, kernel=rbf ..................................
[CV] ...... C=0.1, gamma=0.001, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=0.001, kernel=rbf ..................................
[CV] ...... C=0.1, gamma=0.001, kernel=rbf, score=0.526, total=   0.0s
[CV] C=0.1, gamma=0.001, kernel=rbf ..................................
[CV] ...... C=0.1, gamma=0.001, kernel=rbf, score=0.500, total=   0.0s
[CV] C=0.1, gamma=0.001, kernel=rbf ..................................
[CV] ...... C=0.1, gamma=0.001, kernel=rbf, score=0.500, total=   0.0s
[CV] C=0.1, gamma=0.0001, kernel=rbf .................................
[CV] ..... C=0.1, gamma=0.0001, kernel=rbf, score=0.513, total=   0.0s
[CV] C=0.1, gamma=0.0001, kernel=rbf .................................
[CV] .

[Parallel(n_jobs=1)]: Done 125 out of 125 | elapsed:    1.6s finished


GridSearchCV(cv=None, error_score=nan,
             estimator=SVC(C=1.0, break_ties=False, cache_size=200,
                           class_weight=None, coef0=0.0,
                           decision_function_shape='ovr', degree=3,
                           gamma='scale', kernel='rbf', max_iter=-1,
                           probability=False, random_state=None, shrinking=True,
                           tol=0.001, verbose=False),
             iid='deprecated', n_jobs=None,
             param_grid={'C': [0.1, 1, 10, 100, 1000],
                         'gamma': [1, 0.1, 0.01, 0.001, 0.0001],
                         'kernel': ['rbf']},
             pre_dispatch='2*n_jobs', refit=True, return_train_score=False,
             scoring=None, verbose=3)

In [ ]:
grid.best_params_

{'C': 10, 'gamma': 0.001, 'kernel': 'rbf'}

In [ ]:
grid.best_estimator_

SVC(C=10, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma=0.001, kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)

In [ ]:
svclassifier2 = SVC(C=10, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma=0.001, kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)
svclassifier2.fit(x_train, y_train)

y_svm3 = svclassifier2.predict(x_test)

from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test, y_svm3))
print(classification_report(y_test, y_svm3))
print(f1_score(y_test, y_svm3, average='micro'))

[[15  0  0]
 [ 2 24  1]
 [ 1  6  0]]
              precision    recall  f1-score   support

           0       0.83      1.00      0.91        15
           1       0.80      0.89      0.84        27
           3       0.00      0.00      0.00         7

    accuracy                           0.80        49
   macro avg       0.54      0.63      0.58        49
weighted avg       0.70      0.80      0.74        49

0.7959183673469388


In [ ]:
# SVM - gaussian
from sklearn.svm import SVC
svclassifie = SVC(kernel='rbf', C=100, degree=20, gamma = 0.01)
svclassifie.fit(x_train, y_train)

y_1 = svclassifie.predict(x_test)

from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test,y_1))
print(classification_report(y_test,y_1))
print(f1_score(y_test, y_1, average='micro'))

[[14  1  0]
 [ 0 27  0]
 [ 1  6  0]]
              precision    recall  f1-score   support

           0       0.93      0.93      0.93        15
           1       0.79      1.00      0.89        27
           3       0.00      0.00      0.00         7

    accuracy                           0.84        49
   macro avg       0.58      0.64      0.61        49
weighted avg       0.72      0.84      0.77        49

0.8367346938775511


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [ ]:
%%time

import xgboost as xgb
import matplotlib.pyplot as plt
from xgboost import plot_importance, plot_tree
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split, GridSearchCV

parameters = {
    'n_estimators': [100, 200, 300, 400],
    'learning_rate': [0.001, 0.005, 0.01, 0.05],
    'max_depth': [8, 10, 12, 15],
    'gamma': [0.001, 0.005, 0.01, 0.02],
    'random_state': [42]
}

eval_set = [(x_train, y_train)]
model = xgb.XGBClassifier(eval_set=eval_set, objective='reg:squarederror', verbose=False)
clf = GridSearchCV(model, parameters)

clf.fit(x_train, y_train)

print(f'Best params: {clf.best_params_}')
print(f'Best validation score = {clf.best_score_}')

/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 2 members, which is less than n_splits=5.
  % (min_groups, self.n_splits)), UserWarning)


Best params: {'gamma': 0.005, 'learning_rate': 0.05, 'max_depth': 8, 'n_estimators': 400, 'random_state': 42}
Best validation score = 0.8070175438596492
CPU times: user 32min 4s, sys: 9.68 s, total: 32min 13s
Wall time: 32min 20s


In [ ]:
modelxg = xgb.XGBClassifier(gamma = 0.005, learning_rate = 0.05, max_depth = 8, n_estimators = 400, random_state = 42, objective='reg:squarederror')
modelxg.fit(x_train,y_train, eval_set=eval_set, verbose=False)

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=1, gamma=0.005,
              learning_rate=0.05, max_delta_step=0, max_depth=8,
              min_child_weight=1, missing=None, n_estimators=400, n_jobs=1,
              nthread=None, objective='multi:softprob', random_state=42,
              reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
              silent=None, subsample=1, verbosity=1)

In [ ]:
y_xg = modelxg.predict(x_test)

from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test,y_xg))
print(classification_report(y_test,y_xg))
print(f1_score(y_test, y_xg, average='micro'))

[[15  0  0]
 [ 1 25  1]
 [ 1  6  0]]
              precision    recall  f1-score   support

           0       0.88      1.00      0.94        15
           1       0.81      0.93      0.86        27
           3       0.00      0.00      0.00         7

    accuracy                           0.82        49
   macro avg       0.56      0.64      0.60        49
weighted avg       0.71      0.82      0.76        49

0.8163265306122449


In [ ]:
print('Accuracy score of train data :{}'.format(modelxg.score(x_train,y_train)))

Accuracy score of train data :1.0


In [ ]:
print('Accuracy score of validation data :{}'.format(modelxg.score(x_test,y_test)))

Accuracy score of validation data :0.8163265306122449
